In [1]:
import requests
import pandas as pd
from datetime import datetime
from tqdm import tqdm

BINANCE_CANDLE_COLUMNS = ['opentime', 'openprice', 'highprice', 'lowprice', 'closeprice', 'volume', 'closetime',
                          'quotevolume', 'trades', 'taker_buy_volume', 'taker_buy_quote', 'unused']

def binance_recursive_fetch_2(coins, interval, starttime, endtime, data_type='spot'):
    all_coins_result = {}
    data_list = []
    call_dict = {}
    
    for coin in tqdm(coins):
        result_list = []
        current_time = starttime
        call = 0
        timestamps = []
        
        while current_time < endtime:
            if ((int((endtime - current_time) / (1000 * 60))) + 1) >= 1000:
                limit = 1000
            else:
                limit = int((endtime - current_time) / (1000 * 60) + 1)
            
            if data_type == 'spot':
                url = (f'https://api.binance.com/api/v3/klines'
                       f'?symbol={coin}USDT'
                       f'&startTime={str(current_time)}'
                       f'&interval={interval}'
                       f'&limit={str(limit)}')
            elif data_type == 'futures':
                url = (f'https://fapi.binance.com/fapi/v1/klines'
                       f'?symbol={coin}USDT'
                       f'&startTime={str(current_time)}'
                       f'&interval={interval}'
                       f'&limit={str(limit)}')
            
            result_list += requests.get(url).json()
            
            if result_list:
                # Update current_time with the timestamp of the last data point fetched, plus 1 minute (60000 ms)
                current_time = result_list[-1][0] + 60000
                timestamps.append(current_time)
                call += 1
                
                # Check if the last fetched timestamp is greater than or equal to endtime
                if current_time >= endtime:
                    print(f"Reached endtime at {datetime.fromtimestamp(current_time / 1000).strftime('%Y-%m-%d %H:%M:%S')}. Stopping fetch.")
                    break
                
                print((datetime.fromtimestamp(current_time / 1000).strftime('%Y-%m-%d %H:%M:%S')) + 
                      f' status : {current_time < endtime}, time : {current_time}, limit : {call * 2}')
            
            # Ensure there's no continuous fetching of the same timestamp
            if len(timestamps) > 1 and timestamps[-1] == timestamps[-2]:
                print("Duplicate timestamp detected. Stopping fetch.")
                break
            
            # Sleep if needed to avoid rate limiting (adjust based on your rate limit)
            # time.sleep(0.1)  # Uncomment if needed
            
        current_df = pd.DataFrame(result_list, columns=BINANCE_CANDLE_COLUMNS)
        current_df['coin'] = coin
        current_df = current_df[['coin'] + BINANCE_CANDLE_COLUMNS]
        current_df = current_df.values.tolist()
        
        data_list += current_df
        call_dict.update({coin: call})
    
    return {'data': data_list, 'call': call_dict}

# Set endtime to the current time (today)
endtime = int(datetime.utcnow().timestamp() * 1000)

# # Example usage with today's date as the end time
# sample_spot = binance_recursive_fetch_2(
#     ['USDT'],
#     '1m',
#     starttime=int(pd.to_datetime('2023-01-01 00:00', utc=True).timestamp() * 1000),
#     endtime=endtime,
#     data_type='spot'  # Fetch spot data
# )

# print(sample_spot['data'])

C:\Users\user\AppData\Local\Temp\ipykernel_6768\3312417040.py:74: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  endtime = int(datetime.utcnow().timestamp() * 1000)


In [8]:
# Fetch NEAR USDT
sample_spot = binance_recursive_fetch_2(
    ['ETH'],
    '1h',
    starttime=int(pd.to_datetime('2020-01-01 00:00', utc=True).timestamp() * 1000),
    endtime=endtime,
    data_type='futures'  # Fetch spot data
)

print(sample_spot['data'])

  0%|          | 0/1 [00:00<?, ?it/s]

2020-02-11 23:01:00 status : True, time : 1581433260000, limit : 2
2020-03-24 15:01:00 status : True, time : 1585033260000, limit : 4
2020-05-05 07:01:00 status : True, time : 1588633260000, limit : 6
2020-06-15 23:01:00 status : True, time : 1592233260000, limit : 8
2020-07-27 15:01:00 status : True, time : 1595833260000, limit : 10
2020-09-07 07:01:00 status : True, time : 1599433260000, limit : 12
2020-10-18 23:01:00 status : True, time : 1603033260000, limit : 14
2020-11-29 15:01:00 status : True, time : 1606633260000, limit : 16
2021-01-10 07:01:00 status : True, time : 1610233260000, limit : 18
2021-02-20 23:01:00 status : True, time : 1613833260000, limit : 20
2021-04-03 15:01:00 status : True, time : 1617433260000, limit : 22
2021-05-15 07:01:00 status : True, time : 1621033260000, limit : 24
2021-06-25 23:01:00 status : True, time : 1624633260000, limit : 26
2021-08-06 15:01:00 status : True, time : 1628233260000, limit : 28
2021-09-17 07:01:00 status : True, time : 1631833260

100%|██████████| 1/1 [00:18<00:00, 18.32s/it]

Reached endtime at 2024-12-24 17:01:00. Stopping fetch.
[['ETH', 1577836800000, '129.12', '129.12', '128.62', '128.82', '14947.691', 1577840399999, '1925643.61904', 1249, '7707.625', '992883.79597', '0'], ['ETH', 1577840400000, '128.81', '130.61', '128.76', '130.57', '34755.256', 1577843999999, '4514483.58120', 3116, '19928.267', '2588555.34518', '0'], ['ETH', 1577844000000, '130.58', '130.97', '130.30', '130.80', '21864.946', 1577847599999, '2857377.66035', 1807, '10299.172', '1345961.88773', '0'], ['ETH', 1577847600000, '130.80', '130.82', '129.88', '130.09', '16823.171', 1577851199999, '2190835.34416', 1448, '7580.536', '986901.27252', '0'], ['ETH', 1577851200000, '130.10', '130.63', '130.09', '130.15', '11357.239', 1577854799999, '1480318.82251', 1065, '5204.925', '678301.53122', '0'], ['ETH', 1577854800000, '130.15', '130.37', '130.05', '130.23', '7851.208', 1577858399999, '1022470.85041', 834, '3624.324', '471972.08305', '0'], ['ETH', 1577858400000, '130.23', '130.67', '130.21', 

In [9]:
# Define the column names for the DataFrame based on the Binance API response structure
columns = ['coin', 'opentime', 'openprice', 'highprice', 'lowprice', 'closeprice', 'volume', 'closetime', 
           'quotevolume', 'trades', 'taker_buy_volume', 'taker_buy_quote', 'unused']

# Convert the list of data into a DataFrame
df = pd.DataFrame(sample_spot['data'], columns=columns)

# Show the first few rows of the DataFrame
df

coin       opentime openprice highprice lowprice closeprice     volume  \
0      ETH  1577836800000    129.12    129.12   128.62     128.82  14947.691   
1      ETH  1577840400000    128.81    130.61   128.76     130.57  34755.256   
2      ETH  1577844000000    130.58    130.97   130.30     130.80  21864.946   
3      ETH  1577847600000    130.80    130.82   129.88     130.09  16823.171   
4      ETH  1577851200000    130.10    130.63   130.09     130.15  11357.239   
...    ...            ...       ...       ...      ...        ...        ...   
43661  ETH  1735016400000   3412.22   3433.99  3406.96    3422.61  73286.528   
43662  ETH  1735020000000   3422.62   3425.89  3384.52    3391.88  89769.390   
43663  ETH  1735023600000   3391.87   3414.65  3383.49    3399.92  74621.074   
43664  ETH  1735027200000   3399.91   3415.41  3391.82    3411.98  64264.349   
43665  ETH  1735030800000   3411.98   3413.58  3384.03    3407.29  53502.760   

           closetime      quotevolume  trades taker_buy_volume  \
0      1577840399999    1925643.61904    1249         7707.625   
1      1577843999999    4514483.58120    3116        19928.267   
2      1577847599999    2857377.66035    1807        10299.172   
3      1577851199999    2190835.34416    1448         7580.536   
4      1577854799999    1480318.82251    1065         5204.925   
...              ...              ...     ...              ...   
43661  1735019999999  250629505.64612  132028        36146.655   
43662  1735023599999  305819301.36610  152097        34727.635   
43663  1735027199999  253786268.01971  144182        42480.649   
43664  1735030799999  218766028.04871  156975        28569.486   
43665  1735034399999  181807912.15672  101813        25090.063   

       taker_buy_quote unused  
0         992883.79597      0  
1        2588555.34518      0  
2        1345961.88773      0  
3         986901.27252      0  
4         678301.53122      0  
...                ...    ...  
43661  123614479.59457      0  
43662  118322954.74835      0  
43663  144512685.56531      0  
43664   97279888.05461      0  
43665   85246272.88711      0  

[43666 rows x 13 columns]

In [10]:
df.to_csv('ETH_USDT_futures_data_2020.csv', index=False)

print("DataFrame has been saved to csv")

DataFrame has been saved to csv
